# **Model Fitting**

In [3]:
#imports
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import scipy.stats as stat
from lmfit import Model
from scipy.stats import pearsonr

## Differential

### Reactive Happiness Model (RHM)

In [4]:
data = pd.read_csv('../Data/Lmfit_GBE_Data_Cleaned.csv')

save = {'CR':[], 'EV':[], 'PE':[], 'H':[], 'Certain Reward':[], 'Expected Value':[], 'Prediction Error':[], 'Forgetting Factor':[], 'BIC':[], 'R^2':[]}

# fit each participant
for s in range(0, 50000):

    if len(data[data['participant'] == s] > 0):

        print(s)

        df1 = data[data['participant'] == s]

        CR_data = np.array(df1['certain reward'])[0:]
        EV_data = np.array(df1['expected value'])[0:]
        PE_data = np.array(df1['prediction error'])[0:]
        H_data = np.array(df1['happiness rating'])[0:]

        # calculate change in happiness time series
        H_cleaned = H_data[~np.isnan(H_data)]
        H_change = []
        for i in range(1, len(H_cleaned)):
             H_change.append(H_cleaned[i]-H_cleaned[i-1])
        valid = []
        for i, j in enumerate(H_data):
            if ~np.isnan(j):
                valid.append(int(i))
        # print(H_change)
       
        # model fitting function
        def happiness(CR_coefficient, EV_coefficient, PE_coefficient, F_factor, CR, EV, PE, Valid):
            predictions = np.zeros(11)
            lastCR = CR[0]
            lastEV = EV[0]
            lastPE = PE[0]

            # fit each time point
            for i in range(0,11):
                    k = Valid[i+1]
                    CR_sum = 0
                    EV_sum = 0
                    PE_sum = 0

                    # calculate value signaling time series
                    for j in range(0,int(k)+1):
                        CR_sum += pow(F_factor,(k-j)) * CR[j]
                        EV_sum += pow(F_factor,(k-j)) * EV[j]
                        PE_sum += pow(F_factor,(k-j)) * PE[j]

                    # fitting function
                    predictions[i] = ((CR_sum-lastCR) * CR_coefficient + (EV_sum-lastEV) * EV_coefficient + (PE_sum-lastPE) * PE_coefficient)

                    lastCR = CR_sum
                    lastEV = EV_sum
                    lastPE = PE_sum
            return predictions

        gmodel = Model(happiness, independent_vars=['CR', 'EV', 'PE', 'Valid'])
        params = gmodel.make_params(CR_coefficient=0.05, EV_coefficient=0.05, PE_coefficient=0.1, F_factor=0.5)
        params['CR_coefficient'].set(min = -1, max = 1)
        params['EV_coefficient'].set(min = -1, max = 1)
        params['PE_coefficient'].set(min = -1, max = 1)
        params['F_factor'].set(min = 0, max = 1)
        result = gmodel.fit(H_change, params, CR = CR_data, EV=EV_data, PE=PE_data, Valid=valid)

        # output results
        save['CR'].append(CR_data)
        save['EV'].append(EV_data)
        save['PE'].append(PE_data)
        save['H'].append(H_data)
        save['Certain Reward'].append(result.params['CR_coefficient'].value)
        save['Expected Value'].append(result.params['EV_coefficient'].value)
        save['Prediction Error'].append(result.params['PE_coefficient'].value)
        save['Forgetting Factor'].append(result.params['F_factor'].value)
        save['BIC'].append(result.bic)
        residuals = result.residual
        ss_res = np.sum(residuals**2)
        ss_tot = np.sum((H_change - np.mean(H_change))**2)
        r_squared = 1 - (ss_res / ss_tot)
        print('R^2: ', r_squared)
        save['R^2'].append(r_squared)
save = pd.DataFrame(save)
save.to_csv('../Outputs/Lmfit_RHM_Dif.csv')

1
R^2:  0.4944240028079888
2
R^2:  0.016836279851225044
3
R^2:  0.5356540886363499
4
R^2:  0.4540960670612707
5
R^2:  0.7842298729771076
6
R^2:  0.7452324057574831
7
R^2:  0.34706774012458397
8
R^2:  0.9086152167937592
9
R^2:  0.8218214521459652
10
R^2:  0.7724826937119289
13
R^2:  0.5989631068510404
14
R^2:  0.14313254371532158
15
R^2:  0.655904708451172
16
R^2:  0.8672681751304733
18
R^2:  0.77403492172629
19
R^2:  0.5912705644534824
20
R^2:  0.661810170687424
21
R^2:  0.42044728079056715
22
R^2:  0.8656106625366016
23
R^2:  0.5268606088021961
24
R^2:  0.5455016658157927
25
R^2:  0.6058615067856532
27
R^2:  0.3071070960426716
28
R^2:  0.8358785540084602
29
R^2:  0.18856235858800108
30
R^2:  0.48049645761127535
31
R^2:  0.8652490381027416
32
R^2:  0.37487385140181584
33
R^2:  0.3996319047459822
35
R^2:  0.7907749660042485
36
R^2:  0.33524423068197706
37
R^2:  -0.00805904577086336
38
R^2:  0.3591915279735499
39
R^2:  0.8632885916570058
40
R^2:  0.78971553317497
41
R^2:  0.5916430811949

### DynAffect-C

In [15]:
data = pd.read_csv('../Data/Lmfit_GBE_Data_Cleaned.csv')

save = {'CR':[], 'EV':[], 'PE':[], 'H':[], 'Certain Reward':[], 'Expected Value':[], 'Prediction Error':[], 'Forgetting Factor':[], 'Baseline':[], 'Linear Attraction':[], 'Cubic Attraction':[],  'BIC':[], 'R^2':[]}

# fit each participant
for s in range(0, 50000):

    if len(data[data['participant'] == s] > 0):

        print(s)

        df1 = data[data['participant'] == s]

        CR_data = np.array(df1['certain reward'])[0:]
        EV_data = np.array(df1['expected value'])[0:]
        PE_data = np.array(df1['prediction error'])[0:]
        H_data = np.array(df1['happiness rating'])[0:]

        # calculate change in happiness time series
        H_cleaned = H_data[~np.isnan(H_data)]
        H_change = []
        for i in range(1, len(H_cleaned)):
             H_change.append(H_cleaned[i]-H_cleaned[i-1])
        valid = []
        for i, j in enumerate(H_data):
            if ~np.isnan(j):
                valid.append(int(i))
        # print(H_change)

        # model fitting function
        def happiness(CR_coefficient, EV_coefficient, PE_coefficient, F_factor, Mu, Beta, Alpha, CR, EV, PE, Valid, H_cleaned):
            predictions = np.zeros(11)
            lastCR = CR[0]
            lastEV = EV[0]
            lastPE = PE[0]

            # fit each time point
            for i in range(0,11):
                    k = Valid[i+1]
                    CR_sum = 0
                    EV_sum = 0
                    PE_sum = 0

                    # calculate value signaling time series
                    for j in range(0,int(k)+1):
                            CR_sum += pow(F_factor,(k-j)) * CR[j]
                            EV_sum += pow(F_factor,(k-j)) * EV[j]
                            PE_sum += pow(F_factor,(k-j)) * PE[j]

                    # fitting function
                    predictions[i] = (Mu - H_cleaned[i]) * Beta + pow((Mu - H_cleaned[i]), 3) * Alpha + ((CR_sum-lastCR) * CR_coefficient + (EV_sum-lastEV) * EV_coefficient + (PE_sum-lastPE) * PE_coefficient)
                    lastCR = CR_sum
                    lastEV = EV_sum
                    lastPE = PE_sum
            return predictions


        gmodel = Model(happiness, independent_vars=['CR', 'EV', 'PE', 'Valid', 'H_cleaned'])
        params = gmodel.make_params(CR_coefficient=0.05, EV_coefficient=0.05, PE_coefficient=0.1, Mu = 50, F_factor=0.5, Beta = 0.5, Alpha=0)
        params['CR_coefficient'].set(min = -1, max = 1)
        params['EV_coefficient'].set(min = -1, max = 1)
        params['PE_coefficient'].set(min = -1, max = 1)
        params['F_factor'].set(min = 0, max = 1)
        params['Mu'].set(min = 1, max = 99)
        params['Beta'].set(min = -5, max = 5)
        params['Alpha'].set(min = 0, max = 1)
        result = gmodel.fit(H_change, params, CR = CR_data, EV=EV_data, PE=PE_data, Valid=valid, H_cleaned=H_cleaned)

        # output results
        save['CR'].append(CR_data)
        save['EV'].append(EV_data)
        save['PE'].append(PE_data)
        save['H'].append(H_data)
        save['Certain Reward'].append(result.params['CR_coefficient'].value)
        save['Expected Value'].append(result.params['EV_coefficient'].value)
        save['Prediction Error'].append(result.params['PE_coefficient'].value)
        save['Forgetting Factor'].append(result.params['F_factor'].value)
        save['Baseline'].append(result.params['Mu'].value)
        save['Linear Attraction'].append(result.params['Beta'].value)
        save['Cubic Attraction'].append(result.params['Alpha'].value)
        save['BIC'].append(result.bic)
        residuals = result.residual
        ss_res = np.sum(residuals**2)
        ss_tot = np.sum((H_change - np.mean(H_change))**2)
        r_squared = 1 - (ss_res / ss_tot)
        print('R^2: ', r_squared)
        save['R^2'].append(r_squared)
save = pd.DataFrame(save)
save.to_csv('../Outputs/Lmfit_DC_Dif.csv')

1
R^2:  0.8834884620545581
2
R^2:  0.5040185391842575
3
R^2:  0.8752169625751076
4
R^2:  0.7509476227810554
5
R^2:  0.8401979127213952
6
R^2:  0.8589853584262991
7
R^2:  0.53417563868015
8
R^2:  0.9290757953418253
9
R^2:  0.9373787074163662
10
R^2:  0.7876583564672507
13
R^2:  0.8617415881286321
14
R^2:  0.8953334532140349
15
R^2:  0.7695328060417493
16
R^2:  0.9597876606454878
18
R^2:  0.857319896522594
19
R^2:  0.6293799095072437
20
R^2:  0.9209462081945602
21
R^2:  0.9324522760133344
22
R^2:  0.9234328018491534
23
R^2:  0.7693609344062667
24
R^2:  -0.18593376483536228
25
R^2:  0.6872481903778651
27
R^2:  0.8316913198977827
28
R^2:  0.9594903091714262
29
R^2:  0.9474692918842662
30
R^2:  0.8384902516878626
31
R^2:  0.9640722511729588
32
R^2:  0.4926818531024617
33
R^2:  0.7774706398780322
35
R^2:  0.9558213594706109
36
R^2:  0.9288814370751596
37
R^2:  0.8714471108876269
38
R^2:  0.8436976118544791
39
R^2:  0.9389470678806937
40
R^2:  0.814852623098826
41
R^2:  0.6624638968138151
43


### Linear

In [16]:
data = pd.read_csv('../Data/Lmfit_GBE_Data_Cleaned.csv')

save = {'CR':[], 'EV':[], 'PE':[], 'H':[], 'Certain Reward':[], 'Expected Value':[], 'Prediction Error':[], 'Forgetting Factor':[], 'Baseline':[], 'Linear Attraction':[], 'BIC':[], 'R^2':[]}

# fit each participant
for s in range(0, 50000):

    if len(data[data['participant'] == s] > 0):

        print(s)

        df1 = data[data['participant'] == s]

        CR_data = np.array(df1['certain reward'])[0:]
        EV_data = np.array(df1['expected value'])[0:]
        PE_data = np.array(df1['prediction error'])[0:]
        H_data = np.array(df1['happiness rating'])[0:]

        # calculate change in happiness time series
        H_cleaned = H_data[~np.isnan(H_data)]
        H_change = []
        for i in range(1, len(H_cleaned)):
             H_change.append(H_cleaned[i]-H_cleaned[i-1])
        valid = []
        for i, j in enumerate(H_data):
            if ~np.isnan(j):
                valid.append(int(i))
        # print(H_change)

        # model fitting function
        def happiness(CR_coefficient, EV_coefficient, PE_coefficient, F_factor, Mu, Beta, CR, EV, PE, Valid, H_cleaned):
            predictions = np.zeros(11)
            lastCR = CR[0]
            lastEV = EV[0]
            lastPE = PE[0]

            # fit each time point
            for i in range(0,11):
                    k = Valid[i+1]
                    CR_sum = 0
                    EV_sum = 0
                    PE_sum = 0

                    # calculate value signaling time series
                    for j in range(0,int(k)+1):
                            CR_sum += pow(F_factor,(k-j)) * CR[j]
                            EV_sum += pow(F_factor,(k-j)) * EV[j]
                            PE_sum += pow(F_factor,(k-j)) * PE[j]

                    # fitting function
                    predictions[i] = (Mu - H_cleaned[i]) * Beta + ((CR_sum-lastCR) * CR_coefficient + (EV_sum-lastEV) * EV_coefficient + (PE_sum-lastPE) * PE_coefficient)
                    lastCR = CR_sum
                    lastEV = EV_sum
                    lastPE = PE_sum
            return predictions

        gmodel = Model(happiness, independent_vars=['CR', 'EV', 'PE', 'Valid', 'H_cleaned'])
        params = gmodel.make_params(CR_coefficient=0.05, EV_coefficient=0.05, PE_coefficient=0.1, Mu = 50, F_factor=0.5, Beta = 0.5)
        params['CR_coefficient'].set(min = -1, max = 1)
        params['EV_coefficient'].set(min = -1, max = 1)
        params['PE_coefficient'].set(min = -1, max = 1)
        params['F_factor'].set(min = 0, max = 1)
        params['Mu'].set(min = 1, max = 99)
        params['Beta'].set(min = -5, max = 5)
        result = gmodel.fit(H_change, params, CR = CR_data, EV=EV_data, PE=PE_data, Valid=valid, H_cleaned=H_cleaned)

        # output results
        save['CR'].append(CR_data)
        save['EV'].append(EV_data)
        save['PE'].append(PE_data)
        save['H'].append(H_data)
        save['Certain Reward'].append(result.params['CR_coefficient'].value)
        save['Expected Value'].append(result.params['EV_coefficient'].value)
        save['Prediction Error'].append(result.params['PE_coefficient'].value)
        save['Forgetting Factor'].append(result.params['F_factor'].value)
        save['Baseline'].append(result.params['Mu'].value)
        save['Linear Attraction'].append(result.params['Beta'].value)
        save['BIC'].append(result.bic)
        residuals = result.residual
        ss_res = np.sum(residuals**2)
        ss_tot = np.sum((H_change - np.mean(H_change))**2)
        r_squared = 1 - (ss_res / ss_tot)
        print('R^2: ', r_squared)
        save['R^2'].append(r_squared)
save = pd.DataFrame(save)
save.to_csv('../Outputs/Lmfit_Linear_Dif.csv')

1
R^2:  0.8619720033177578
2
R^2:  0.5040185426247339
3
R^2:  0.8641444318038476
4
R^2:  0.7509476229596617
5
R^2:  0.8402046971763701
6
R^2:  0.8013229829043873
7
R^2:  0.5574308236681323
8
R^2:  0.9290758270045589
9
R^2:  0.937378708729311
10
R^2:  0.7876583565201163
13
R^2:  0.8617415881536108
14
R^2:  0.7890713933299571
15
R^2:  0.7695328074044654
16
R^2:  0.9175111939436859
18
R^2:  0.857319936302211
19
R^2:  0.6293799094969545
20
R^2:  0.8870002868259547
21
R^2:  0.9217032852779589
22
R^2:  0.9058124727549841
23
R^2:  0.7469027491994487
24
R^2:  0.666282779369666
25
R^2:  0.687248191502432
27
R^2:  0.8262939147846515
28
R^2:  0.9305046939942881
29
R^2:  0.7351221407735005
30
R^2:  0.8384902791714592
31
R^2:  0.9640722511982462
32
R^2:  0.4909190747422637
33
R^2:  0.7577341064385258
35
R^2:  0.9484315363427537
36
R^2:  0.9278790966119933
37
R^2:  0.7557929838464827
38
R^2:  0.7258703724535397
39
R^2:  0.9389470686080804
40
R^2:  0.8148526387142495
41
R^2:  0.6624638938144324
43
R^

## Non-Differential

### RHM

In [17]:
data = pd.read_csv('../Data/Lmfit_GBE_Data_Cleaned.csv')

save = {'CR':[], 'EV':[], 'PE':[], 'H':[], 'Certain Reward':[], 'Expected Value':[], 'Prediction Error':[], 'Forgetting Factor':[], 'Baseline':[],'BIC':[], 'R^2':[]}

# fit each participant
for s in range(0, 50000):
    if len(data[data['participant'] == s] > 0):

        print(s)

        df1 = data[data['participant'] == s]

        CR_data = np.array(df1['certain reward'])[0:]
        EV_data = np.array(df1['expected value'])[0:]
        PE_data = np.array(df1['prediction error'])[0:]
        H_data = np.array(df1['happiness rating'])[0:]

        # remove first happiness value
        H_cleaned = H_data[~np.isnan(H_data)]
        H_cleaned = H_cleaned[1:]
        valid = []
        for i, j in enumerate(H_data):
            if ~np.isnan(j):
                valid.append(int(i))
        # print(valid)
        # print(H_cleaned)

        # model fitting function
        def happiness(CR_coefficient, EV_coefficient, PE_coefficient, F_factor, Mu, CR, EV, PE, Valid):
            predictions = np.zeros(11)

            # fit each time point
            for i in range(0,11):
                    k = Valid[i+1]
                    CR_sum = 0
                    EV_sum = 0
                    PE_sum = 0

                    # calculate value signaling time series
                    for j in range(0,int(k)+1):
                            CR_sum += pow(F_factor,(k-j)) * CR[j]
                            EV_sum += pow(F_factor,(k-j)) * EV[j]
                            PE_sum += pow(F_factor,(k-j)) * PE[j]

                    # fitting function
                    predictions[i] = Mu + (CR_sum * CR_coefficient + EV_sum * EV_coefficient + PE_sum * PE_coefficient)
            return predictions

        gmodel = Model(happiness, independent_vars=['CR', 'EV', 'PE', 'Valid'])
        params = gmodel.make_params(CR_coefficient=0.05, EV_coefficient=0.05, PE_coefficient=0.1, Mu = 50, F_factor=0.5)
        params['CR_coefficient'].set(min = -1, max = 1)
        params['EV_coefficient'].set(min = -1, max = 1)
        params['PE_coefficient'].set(min = -1, max = 1)
        params['F_factor'].set(min = 0, max = 1)
        params['Mu'].set(min = 1, max = 99)
        result = gmodel.fit(H_cleaned, params, CR = CR_data, EV=EV_data, PE=PE_data, Valid=valid)

        # output results
        save['CR'].append(CR_data)
        save['EV'].append(EV_data)
        save['PE'].append(PE_data)
        save['H'].append(H_data)
        save['Certain Reward'].append(result.params['CR_coefficient'].value)
        save['Expected Value'].append(result.params['EV_coefficient'].value)
        save['Prediction Error'].append(result.params['PE_coefficient'].value)
        save['Forgetting Factor'].append(result.params['F_factor'].value)
        save['Baseline'].append(result.params['Mu'].value)
        save['BIC'].append(result.bic)
        residuals = result.residual
        ss_res = np.sum(residuals**2)
        ss_tot = np.sum((H_cleaned - np.mean(H_cleaned))**2)
        r_squared = 1 - (ss_res / ss_tot)
        print('R^2: ', r_squared)
        save['R^2'].append(r_squared)
save = pd.DataFrame(save)
save.to_csv('../Outputs/Lmfit_RHM_NonDif.csv')

1
R^2:  0.7138120874740208
2
R^2:  0.3822270830824738
3
R^2:  0.4231879943754895
4
R^2:  0.7332657902019997
5
R^2:  0.729238661638095
6
R^2:  0.8282734835972121
7
R^2:  0.47535839426362647
8
R^2:  0.8890876383906668
9
R^2:  0.6354351811894154
10
R^2:  0.8512623237191135
13
R^2:  0.6453533432175796
14
R^2:  0.5694977339969642
15
R^2:  0.643967518312162
16
R^2:  0.9110603636283379
18
R^2:  0.45165678786945107
19
R^2:  0.4847233701808158
20
R^2:  0.5793642024761796
21
R^2:  0.3207615529663732
22
R^2:  0.8309753251688616
23
R^2:  0.528344734566683
24
R^2:  0.5466972507501915
25
R^2:  0.9299808487060731
27
R^2:  0.4632903139840414
28
R^2:  0.8461299236864497
29
R^2:  0.5376820182686889
30
R^2:  0.20254620860520867
31
R^2:  0.9158012887597798
32
R^2:  0.631152292206492
33
R^2:  0.655091183359384
35
R^2:  0.8101635136567562
36
R^2:  0.9332593907554272
37
R^2:  0.8831919362242315
38
R^2:  0.43968667218837376
39
R^2:  0.8870096748655618
40
R^2:  0.821904608913305
41
R^2:  0.6855133128930778
43


### DynAffect-C

In [19]:
data = pd.read_csv('../Data/Lmfit_GBE_Data_Cleaned.csv')

save = {'CR':[], 'EV':[], 'PE':[], 'H':[], 'Certain Reward':[], 'Expected Value':[], 'Prediction Error':[], 'Forgetting Factor':[], 'Baseline':[], 'Linear Attraction':[], 'Cubic Attraction':[], 'BIC':[], 'R^2':[]}

# fit each participant
for s in range(0, 50000):

    if len(data[data['participant'] == s] > 0):

        print(s)

        df1 = data[data['participant'] == s]

        CR_data = np.array(df1['certain reward'])[0:]
        EV_data = np.array(df1['expected value'])[0:]
        PE_data = np.array(df1['prediction error'])[0:]
        H_data = np.array(df1['happiness rating'])[0:]

        # remove first happiness value
        H_cleaned = H_data[~np.isnan(H_data)]
        H_cleaned2 = H_cleaned[1:]
        valid = []
        for i, j in enumerate(H_data):
            if ~np.isnan(j):
                valid.append(int(i))
        # print(valid)
        # print(H_cleaned)

        # model fitting function
        def happiness(CR_coefficient, EV_coefficient, PE_coefficient, Mu, F_factor, Beta, Alpha, CR, EV, PE, Valid, H_cleaned):
            predictions = np.zeros(11)

            # fit each time point
            for i in range(0,11):
                    k = Valid[i+1]
                    CR_sum = 0
                    EV_sum = 0
                    PE_sum = 0


                    # calculate value signaling time series
                    for j in range(0,int(k)+1):
                        CR_sum += pow(F_factor,(k-j)) * CR[j]
                        EV_sum += pow(F_factor,(k-j)) * EV[j]
                        PE_sum += pow(F_factor,(k-j)) * PE[j]

                    # fitting function
                    predictions[i] = Mu - ((Mu - H_cleaned[i]) * np.exp(-1*Beta))/np.sqrt(1+(Alpha/Beta)*np.power(Mu-H_cleaned[i],2)*(1-np.exp(-2*Beta))) + (CR_sum * CR_coefficient + EV_sum * EV_coefficient + PE_sum * PE_coefficient)
            return predictions

        gmodel = Model(happiness, independent_vars=['CR', 'EV', 'PE', 'Valid', 'H_cleaned'])
        params = gmodel.make_params(CR_coefficient=0.05, EV_coefficient=0.05, PE_coefficient=0.1, Mu = 50, F_factor=0.5, Beta = 0.5, Alpha=0)
        params['CR_coefficient'].set(min = -1, max = 1)
        params['EV_coefficient'].set(min = -1, max = 1)
        params['PE_coefficient'].set(min = -1, max = 1)
        params['F_factor'].set(min = 0, max = 1)
        params['Mu'].set(min = 1, max = 99)
        params['Beta'].set(min = -5, max = 5)
        params['Alpha'].set(min = 0, max = 1)
        result = gmodel.fit(H_cleaned2, params, CR = CR_data, EV=EV_data, PE=PE_data, Valid=valid, H_cleaned = H_cleaned)

        # output results
        save['CR'].append(CR_data)
        save['EV'].append(EV_data)
        save['PE'].append(PE_data)
        save['H'].append(H_data)
        save['Certain Reward'].append(result.params['CR_coefficient'].value)
        save['Expected Value'].append(result.params['EV_coefficient'].value)
        save['Prediction Error'].append(result.params['PE_coefficient'].value)
        save['Forgetting Factor'].append(result.params['F_factor'].value)
        save['Baseline'].append(result.params['Mu'].value)
        save['Linear Attraction'].append(result.params['Beta'].value)
        save['Cubic Attraction'].append(result.params['Alpha'].value)
        save['BIC'].append(result.bic)
        residuals = result.residual
        ss_res = np.sum(residuals**2)
        ss_tot = np.sum((H_cleaned2 - np.mean(H_cleaned2))**2)
        r_squared = 1 - (ss_res / ss_tot)
        print('R^2: ', r_squared)
        save['R^2'].append(r_squared)
save = pd.DataFrame(save)
save.to_csv('../Outputs/Lmfit_DC_NonDif.csv')

1
R^2:  0.7136741953807867
2
R^2:  0.39713493845348036
3
R^2:  0.4229809955799274
4
R^2:  0.7338330416720809
5
R^2:  0.729118455553003
6
R^2:  0.8460704412021584
7
R^2:  0.6661939850623053
8
R^2:  0.9247684450277156
9
R^2:  0.6346639380296478
10
R^2:  0.8512568084176609
13
R^2:  0.6442614598615686
14
R^2:  0.5679479549132864
15
R^2:  0.6431266023428065
16
R^2:  0.9599171487635264
18
R^2:  0.45825015242192757
19
R^2:  0.6173806706312792
20
R^2:  0.5780271683373829
21
R^2:  0.31925053995263397
22
R^2:  0.7236535313763458
23
R^2:  0.8978861747404849
24
R^2:  0.5022504276631847
25
R^2:  0.9713359742300235
27
R^2:  0.4910832716287016
28
R^2:  0.8460530463901078
29
R^2:  0.5373278049394141
30
R^2:  0.7232216888216623
31
R^2:  0.9156708377038777
32
R^2:  0.6303151713880117
33
R^2:  0.6598012329897864
35
R^2:  0.8585749834564833
36
R^2:  0.9365211145108089
37
R^2:  0.8831892594134705
38
R^2:  0.5950550192528486
39
R^2:  0.8867157085656295
40
R^2:  0.968133968676586
41
R^2:  0.7028524961950979


### Linear

In [20]:
data = pd.read_csv('../Data/Lmfit_GBE_Data_Cleaned.csv')

save = {'CR':[], 'EV':[], 'PE':[], 'H':[], 'Certain Reward':[], 'Expected Value':[], 'Prediction Error':[], 'Forgetting Factor':[], 'Baseline':[], 'Linear Attraction':[], 'BIC':[], 'R^2':[]}

# fit each participant
for s in range(0, 50000):

    if len(data[data['participant'] == s] > 0):

        print(s)

        df1 = data[data['participant'] == s]

        CR_data = np.array(df1['certain reward'])[0:]
        EV_data = np.array(df1['expected value'])[0:]
        PE_data = np.array(df1['prediction error'])[0:]
        H_data = np.array(df1['happiness rating'])[0:]

        # remove first happiness value
        H_cleaned = H_data[~np.isnan(H_data)]
        H_cleaned2 = H_cleaned[1:]
        valid = []
        for i, j in enumerate(H_data):
            if ~np.isnan(j):
                valid.append(int(i))
        # print(valid)
        # print(H_cleaned)

        # model fitting function
        def happiness(CR_coefficient, EV_coefficient, PE_coefficient, Mu, F_factor, Beta, CR, EV, PE, Valid, H_cleaned):
            predictions = np.zeros(11)

            # fit each time point
            for i in range(0,11):
                    k = Valid[i+1]
                    CR_sum = 0
                    EV_sum = 0
                    PE_sum = 0

                    # calculate value signaling time series
                    for j in range(0,int(k)+1):
                        CR_sum += pow(F_factor,(k-j)) * CR[j]
                        EV_sum += pow(F_factor,(k-j)) * EV[j]
                        PE_sum += pow(F_factor,(k-j)) * PE[j]

                    # fitting function
                    predictions[i] = Mu + (H_cleaned[i] - Mu)* np.exp(-1*Beta) + (CR_sum * CR_coefficient + EV_sum * EV_coefficient + PE_sum * PE_coefficient)
            return predictions

        gmodel = Model(happiness, independent_vars=['CR', 'EV', 'PE', 'Valid', 'H_cleaned'])
        params = gmodel.make_params(CR_coefficient=0.05, EV_coefficient=0.05, PE_coefficient=0.1, Mu = 50, F_factor=0.5, Beta = 0.5)
        params['CR_coefficient'].set(min = -1, max = 1)
        params['EV_coefficient'].set(min = -1, max = 1)
        params['PE_coefficient'].set(min = -1, max = 1)
        params['F_factor'].set(min = 0, max = 1)
        params['Mu'].set(min = 1, max = 99)
        params['Beta'].set(min = -5, max = 5)
        result = gmodel.fit(H_cleaned2, params, CR = CR_data, EV=EV_data, PE=PE_data, Valid=valid, H_cleaned = H_cleaned)

        # output results
        save['CR'].append(CR_data)
        save['EV'].append(EV_data)
        save['PE'].append(PE_data)
        save['H'].append(H_data)
        save['Certain Reward'].append(result.params['CR_coefficient'].value)
        save['Expected Value'].append(result.params['EV_coefficient'].value)
        save['Prediction Error'].append(result.params['PE_coefficient'].value)
        save['Forgetting Factor'].append(result.params['F_factor'].value)
        save['Baseline'].append(result.params['Mu'].value)
        save['Linear Attraction'].append(result.params['Beta'].value)
        save['BIC'].append(result.bic)
        residuals = result.residual
        ss_res = np.sum(residuals**2)
        ss_tot = np.sum((H_cleaned2 - np.mean(H_cleaned2))**2)
        r_squared = 1 - (ss_res / ss_tot)
        print('R^2: ', r_squared)
        save['R^2'].append(r_squared)
save = pd.DataFrame(save)
save.to_csv('../Outputs/Lmfit_Linear_NonDif.csv')

1
R^2:  0.7123822071105889
2
R^2:  0.5369639229180401
3
R^2:  0.41927040532824034
4
R^2:  0.7338438134151377
5
R^2:  0.6616465155172266
6
R^2:  0.8386232377903975
7
R^2:  0.6661947062976321
8
R^2:  0.9397351823740085
9
R^2:  0.6320487401841482
10
R^2:  0.8491127149512749
13
R^2:  0.6412185830545358
14
R^2:  0.5647388451927183
15
R^2:  0.642945619582493
16
R^2:  0.9111193716990748
18
R^2:  0.5254537815977954
19
R^2:  0.48536102355634225
20
R^2:  0.5761758630792568
21
R^2:  0.3101194641318471
22
R^2:  0.6285942265971289
23
R^2:  0.8067287456459926
24
R^2:  0.4996630444315957
25
R^2:  0.9153261679124013
27
R^2:  0.49226414583893974
28
R^2:  0.8459124379477041
29
R^2:  0.5327700291951623
30
R^2:  0.8036493000898546
31
R^2:  0.9154385855999119
32
R^2:  0.6292228005166687
33
R^2:  0.6571761996371142
35
R^2:  0.8344037100555344
36
R^2:  0.9361868067633908
37
R^2:  0.8832331999854615
38
R^2:  0.5953273715014117
39
R^2:  0.8845227121177531
40
R^2:  0.9681357980612876
41
R^2:  0.7028525034873168

### RHM, seven-back

In [22]:
data = pd.read_csv('../Data/Lmfit_GBE_Data_Cleaned.csv')

save = {'CR':[], 'EV':[], 'PE':[], 'H':[], 'Certain Reward':[], 'Expected Value':[], 'Prediction Error':[], 'Forgetting Factor':[], 'Baseline':[],'BIC':[], 'R^2':[]}

# fit each participant
for s in range(0, 50000):

    if len(data[data['participant'] == s] > 0):

        print(s)

        df1 = data[data['participant'] == s]

        CR_data = np.array(df1['certain reward'])[0:]
        EV_data = np.array(df1['expected value'])[0:]
        PE_data = np.array(df1['prediction error'])[0:]
        H_data = np.array(df1['happiness rating'])[0:]

        # remove first happiness value
        H_cleaned = H_data[~np.isnan(H_data)]
        H_cleaned = H_cleaned[1:]
        valid = []
        for i, j in enumerate(H_data):
            if ~np.isnan(j):
                valid.append(int(i))
        # print(valid)
        # print(H_cleaned)

        # model fitting function
        def happiness(CR_coefficient, EV_coefficient, PE_coefficient, F_factor, Mu, CR, EV, PE, Valid):
            predictions = np.zeros(11)

            # fit each time point
            for i in range(0,11):
                    k = Valid[i+1]
                    CR_sum = 0
                    EV_sum = 0
                    PE_sum = 0

                    # calculate value signaling time series
                    for j in range(0,int(k)+1):
                        if (k-j < 7):
                            CR_sum += pow(F_factor,(k-j)) * CR[j]
                            EV_sum += pow(F_factor,(k-j)) * EV[j]
                            PE_sum += pow(F_factor,(k-j)) * PE[j]
                    
                    # fitting function
                    predictions[i] = Mu + (CR_sum * CR_coefficient + EV_sum * EV_coefficient + PE_sum * PE_coefficient)
            return predictions

        gmodel = Model(happiness, independent_vars=['CR', 'EV', 'PE', 'Valid'])
        params = gmodel.make_params(CR_coefficient=0.05, EV_coefficient=0.05, PE_coefficient=0.1, Mu = 50, F_factor=0.5)
        params['CR_coefficient'].set(min = -1, max = 1)
        params['EV_coefficient'].set(min = -1, max = 1)
        params['PE_coefficient'].set(min = -1, max = 1)
        params['F_factor'].set(min = 0, max = 1)
        params['Mu'].set(min = 1, max = 99)
        result = gmodel.fit(H_cleaned, params, CR = CR_data, EV=EV_data, PE=PE_data, Valid=valid)

        # output results
        save['CR'].append(CR_data)
        save['EV'].append(EV_data)
        save['PE'].append(PE_data)
        save['H'].append(H_data)
        save['Certain Reward'].append(result.params['CR_coefficient'].value)
        save['Expected Value'].append(result.params['EV_coefficient'].value)
        save['Prediction Error'].append(result.params['PE_coefficient'].value)
        save['Forgetting Factor'].append(result.params['F_factor'].value)
        save['Baseline'].append(result.params['Mu'].value)
        save['BIC'].append(result.bic)
        residuals = result.residual
        ss_res = np.sum(residuals**2)
        ss_tot = np.sum((H_cleaned - np.mean(H_cleaned))**2)
        r_squared = 1 - (ss_res / ss_tot)
        print('R^2: ', r_squared)
        save['R^2'].append(r_squared)
save = pd.DataFrame(save)
save.to_csv('../Outputs/Lmfit_RHM_NonDif_<7.csv')

1
R^2:  0.7138285020803262
2
R^2:  0.3963619856496913
3
R^2:  0.5373482716768081
4
R^2:  0.7306844655252385
5
R^2:  0.6570866415706129
6
R^2:  0.8151026540822719
7
R^2:  0.5076124740094619
8
R^2:  0.8890971761899258
9
R^2:  0.6354352448892258
10
R^2:  0.5792096878130277
13
R^2:  0.6477283584156883
14
R^2:  0.5643067661479366
15
R^2:  0.6447584671168062
16
R^2:  0.9080468693005983
18
R^2:  0.45165558058086297
19
R^2:  0.3632515005097047
20
R^2:  0.7188992458882975
21
R^2:  0.3214349114517181
22
R^2:  0.6053816532431537
23
R^2:  0.43861390140269507
24
R^2:  0.474622682060833
25
R^2:  0.7724240558012793
27
R^2:  0.4632903137729316
28
R^2:  0.7701024832773167
29
R^2:  0.894442331495696
30
R^2:  0.2025462104543314
31
R^2:  0.9158009798837576
32
R^2:  0.44063475960340837
33
R^2:  0.6550911832097823
35
R^2:  0.8101868097191557
36
R^2:  0.9334979548908298
37
R^2:  0.7334512319195581
38
R^2:  0.47741718586531234
39
R^2:  0.8870096748739134
40
R^2:  0.8219009550257974
41
R^2:  0.4765768910451643

### DynAffect-C, Seven-back

In [23]:
data = pd.read_csv('../Data/Lmfit_GBE_Data_Cleaned.csv')

save = {'CR':[], 'EV':[], 'PE':[], 'H':[], 'Certain Reward':[], 'Expected Value':[], 'Prediction Error':[], 'Forgetting Factor':[], 'Baseline':[], 'Linear Attraction':[], 'Cubic Attraction':[], 'BIC':[], 'R^2':[]}

# fit each participant
for s in range(0, 50000):

    if len(data[data['participant'] == s] > 0):

        print(s)

        df1 = data[data['participant'] == s]

        CR_data = np.array(df1['certain reward'])[0:]
        EV_data = np.array(df1['expected value'])[0:]
        PE_data = np.array(df1['prediction error'])[0:]
        H_data = np.array(df1['happiness rating'])[0:]

        # remove first happiness value
        H_cleaned = H_data[~np.isnan(H_data)]
        H_cleaned2 = H_cleaned[1:]
        valid = []
        for i, j in enumerate(H_data):
            if ~np.isnan(j):
                valid.append(int(i))
        # print(valid)
        # print(H_cleaned)

        # model fitting function
        def happiness(CR_coefficient, EV_coefficient, PE_coefficient, Mu, F_factor, Beta, Alpha, CR, EV, PE, Valid, H_cleaned):
            predictions = np.zeros(11)

            # fit each time point
            for i in range(0,11):
                    k = Valid[i+1]
                    CR_sum = 0
                    EV_sum = 0
                    PE_sum = 0
                    for j in range(0,int(k)+1):
                        if(k-j < 7):
                            CR_sum += pow(F_factor,(k-j)) * CR[j]
                            EV_sum += pow(F_factor,(k-j)) * EV[j]
                            PE_sum += pow(F_factor,(k-j)) * PE[j]
                    predictions[i] = Mu - ((Mu - H_cleaned[i]) * np.exp(-1*Beta))/np.sqrt(1+(Alpha/Beta)*np.power(Mu-H_cleaned[i],2)*(1-np.exp(-2*Beta))) + (CR_sum * CR_coefficient + EV_sum * EV_coefficient + PE_sum * PE_coefficient)
            return predictions

        gmodel = Model(happiness, independent_vars=['CR', 'EV', 'PE', 'Valid', 'H_cleaned'])
        params = gmodel.make_params(CR_coefficient=0.05, EV_coefficient=0.05, PE_coefficient=0.1, Mu = 50, F_factor=0.5, Beta = 0.5, Alpha=0)
        params['CR_coefficient'].set(min = -1, max = 1)
        params['EV_coefficient'].set(min = -1, max = 1)
        params['PE_coefficient'].set(min = -1, max = 1)
        params['F_factor'].set(min = 0, max = 1)
        params['Mu'].set(min = 1, max = 99)
        params['Beta'].set(min = -5, max = 5)
        params['Alpha'].set(min = 0, max = 1)
        result = gmodel.fit(H_cleaned2, params, CR = CR_data, EV=EV_data, PE=PE_data, Valid=valid, H_cleaned = H_cleaned)

        # output results
        save['CR'].append(CR_data)
        save['EV'].append(EV_data)
        save['PE'].append(PE_data)
        save['H'].append(H_data)
        save['Certain Reward'].append(result.params['CR_coefficient'].value)
        save['Expected Value'].append(result.params['EV_coefficient'].value)
        save['Prediction Error'].append(result.params['PE_coefficient'].value)
        save['Forgetting Factor'].append(result.params['F_factor'].value)
        save['Baseline'].append(result.params['Mu'].value)
        save['Linear Attraction'].append(result.params['Beta'].value)
        save['Cubic Attraction'].append(result.params['Alpha'].value)
        save['BIC'].append(result.bic)
        residuals = result.residual
        ss_res = np.sum(residuals**2)
        ss_tot = np.sum((H_cleaned2 - np.mean(H_cleaned2))**2)
        r_squared = 1 - (ss_res / ss_tot)
        print('R^2: ', r_squared)
        save['R^2'].append(r_squared)
save = pd.DataFrame(save)
save.to_csv('../Outputs/Lmfit_DC_NonDif_<7.csv')

1
R^2:  0.7136892604619776
2
R^2:  0.4102881938782079
3
R^2:  0.5369977927603098
4
R^2:  0.7318201974229801
5
R^2:  0.8514745191722096
6
R^2:  0.8407878281442711
7
R^2:  0.6661947059623854
8
R^2:  0.9395979718886325
9
R^2:  0.634663748068131
10
R^2:  0.6673427416400957
13
R^2:  0.6469869889256065
14
R^2:  0.5631363235239812
15
R^2:  0.6438944895029178
16
R^2:  0.9599200885316496
18
R^2:  0.5165520406441894
19
R^2:  0.40948860273216325
20
R^2:  0.5843663624200358
21
R^2:  0.31989425626331747
22
R^2:  0.7276298751326981
23
R^2:  0.8997622118066024
24
R^2:  0.47797159468805783
25
R^2:  0.9713360195903292
27
R^2:  0.4915470598045686
28
R^2:  0.8928816686935421
29
R^2:  0.9042733209632714
30
R^2:  0.6743679567756823
31
R^2:  0.915656929873389
32
R^2:  0.5967820925502819
33
R^2:  0.6557252390337402
35
R^2:  0.8586490564694826
36
R^2:  0.9366781278942298
37
R^2:  0.7520896793105905
38
R^2:  0.5952958862874665
39
R^2:  0.8865996568571735
40
R^2:  0.9681084293175326
41
R^2:  0.7028523101253725
